In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
import matplotlib.pyplot as plt

# import k-means from clustering stage
from sklearn.cluster import KMeans

from sklearn.metrics import silhouette_score

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [2]:
DN_GEO=pd.read_csv('DN_GEO.csv')
print('Data downloaded!')

Data downloaded!


In [3]:
DN_GEO.head()

Districts Neighbourhood   Latitude  Longitude
0  North West Delhi  Adarsh Nagar  28.714200  77.166710
1  North West Delhi   Ashok Vihar  28.692060  77.177550
2  North West Delhi       Azadpur  28.705300  77.178300
3  North West Delhi        Bawana  28.802210  77.040199
4  North West Delhi     Begum Pur  28.536978  77.209941

In [4]:
DN_GEO['Districts'].value_counts().to_frame()

Districts
South Delhi              48
North Delhi              27
South West Delhi         21
West Delhi               20
East Delhi               19
North West Delhi         18
North East Delhi         13
New Delhi                10
Central Delhi             8

In [5]:
DN_GEO.shape

(184, 4)

In [6]:
print(DN_GEO.Districts.unique())

['North West Delhi' 'North Delhi' 'North East Delhi' 'Central Delhi'
 'New Delhi' 'East Delhi' 'South Delhi' 'South West Delhi' 'West Delhi']


In [7]:
DN_GEO.isnull().sum()

Districts        0
Neighbourhood    0
Latitude         0
Longitude        0
dtype: int64

In [8]:
import time
start_time = time.time()

address = 'Delhi, INDIA'

geolocator = Nominatim(user_agent="Jupyter")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Delhi City are {}, {}.'.format(latitude, longitude))

print("--- %s seconds ---" % round((time.time() - start_time), 2))

The geograpical coordinate of Delhi City are 28.6517178, 77.2219388.
--- 0.42 seconds ---


In [9]:
# create map of Toronto using latitude and longitude values
map_Delhi = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, districts, Neighbourhood in zip(DN_GEO['Latitude'], DN_GEO['Longitude'], DN_GEO['Districts'], DN_GEO['Neighbourhood']):
    label = '{}, {}'.format(Neighbourhood, districts)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Delhi)  
    
map_Delhi

In [10]:
CLIENT_ID = 'OLN1BAQQBHO234LKFIU1ZNGV4Z3O3P1GS5KIMTNPJHLX1MKL' # your Foursquare ID
CLIENT_SECRET = 'VDM5CGGVSUOGKMY21ETO4J1UAJH5QJEALQCJAIWUF2DJXR2T' # your Foursquare Secret
VERSION = '20181218' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: OLN1BAQQBHO234LKFIU1ZNGV4Z3O3P1GS5KIMTNPJHLX1MKL
CLIENT_SECRET:VDM5CGGVSUOGKMY21ETO4J1UAJH5QJEALQCJAIWUF2DJXR2T


In [11]:
def getNearbyVenues(names, latitudes, longitudes, LIMIT=200, radius=1000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [12]:
D_venues = getNearbyVenues(names=DN_GEO['Neighbourhood'],
                                  latitudes=DN_GEO['Latitude'],
                                  longitudes=DN_GEO['Longitude'],
                                  LIMIT=200)

print('The "D_venues" dataframe has {} venues and {} unique venue types.'.format(
      len(D_venues['Venue Category']),
      len(D_venues['Venue Category'].unique())))

D_venues.to_csv('D_venues.csv', sep=',', encoding='UTF8')
D_venues.head()

Adarsh Nagar
Ashok Vihar
Azadpur
Bawana
Begum Pur
Dhaka
Jahangirpuri
Karala
Keshav Puram
Kingsway Camp
Kohat Enclave
Model Town
Narela
Pitam Pura
Rani Bagh
Rithala
Rohini Sub City
Shalimar Bagh
Shakti Nagar
Bara Hindu Rao
Chandni Chowk
Chawri Bazaar
Civil Lines
Dariba Kalan
Ghantewala
Gulabi Bagh
Kamla Nagar
Kashmiri Gate
Kotwali
Lahori Gate
Nehru Vihar
Paharganj
Pratap Nagar
Pul Bangash
Roshanara Bagh
Sadar Bazaar
Sangam Vihar
Sant Nagar
Sarai Kale Khan
Sarai Rohilla
Shakti Nagar
Shastri Nagar
Tees Hazari
Timarpur
Wazirabad
Babarpur
Dilshad Garden
Kabir Nagar
Mandoli
Maujpur
Nand Nagri
Naveen Shahdara
New Usmanpur
Sadatpur
Shahdara
Sonia Vihar
Shastri Park
Yamuna Vihar
Chandni Chowk
Daryaganj
Jhandewalan
Karol Bagh
Bara Hindu Rao
Paharganj
Rajender Nagar
Sadar Bazaar
Barakhamba Road
Chanakyapuri
Connaught Place
Gautampuri
Gole Market
Golf Links
INA Colony
Khan Market
Laxmibai Nagar
Pragati Maidan
Brij Puri
East Vinod Nagar
Gandhi Nagar
Geeta Colony
Jhilmil Colony
Krishna Nagar
Laxmi N

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Adarsh Nagar                 28.7142                 77.16671   
1  Adarsh Nagar                 28.7142                 77.16671   
2  Adarsh Nagar                 28.7142                 77.16671   
3  Adarsh Nagar                 28.7142                 77.16671   
4  Adarsh Nagar                 28.7142                 77.16671   

                        Venue  Venue Latitude  Venue Longitude  \
0          Shalimar bagh club       28.711882        77.157933   
1                   Ever Bake       28.706419        77.162607   
2              Domino's Pizza       28.706000        77.163000   
3             Cafe Coffee Day       28.707934        77.161478   
4  Adarsh Nagar Metro Station       28.716598        77.170436   

       Venue Category  
0   Indian Restaurant  
1              Bakery  
2         Pizza Place  
3         Coffee Shop  
4  Light Rail Station

In [13]:
colnames = ['Neighbourhood', 'Neighbourhood Latitude', 'Neighbourhood Longitude', 'Venue', 'Venue Latitude', 'Venue Longitude', 'Venue Category']
D_venues = pd.read_csv('D_venues.csv', skiprows=1, names=colnames)
D_venues.columns = D_venues.columns.str.replace(' ', '')
D_venues.head()

Neighbourhood  NeighbourhoodLatitude  NeighbourhoodLongitude  \
0  Adarsh Nagar                28.7142                77.16671   
1  Adarsh Nagar                28.7142                77.16671   
2  Adarsh Nagar                28.7142                77.16671   
3  Adarsh Nagar                28.7142                77.16671   
4  Adarsh Nagar                28.7142                77.16671   

                        Venue  VenueLatitude  VenueLongitude  \
0          Shalimar bagh club      28.711882       77.157933   
1                   Ever Bake      28.706419       77.162607   
2              Domino's Pizza      28.706000       77.163000   
3             Cafe Coffee Day      28.707934       77.161478   
4  Adarsh Nagar Metro Station      28.716598       77.170436   

        VenueCategory  
0   Indian Restaurant  
1              Bakery  
2         Pizza Place  
3         Coffee Shop  
4  Light Rail Station

In [14]:
D_venues.shape

(3213, 7)

In [15]:
def Venues_Map(Borough_name, Borough_neighborhoods):
    
    # Use geopy library to get the latitude and longitude values 
    geolocator = Nominatim(user_agent="Jupyter")
    Borough_location = geolocator.geocode(Borough_name) #'Brooklyn, NY'
    Borough_latitude = Borough_location.latitude
    Borough_longitude = Borough_location.longitude
    print('The geographical coordinates of "{}" are {}, {}.'.format(Borough_name, Borough_latitude, Borough_longitude))
    
    # To verify the number of Boroughs and Neighborhoods in the extracted data
    print('The "{}" dataframe has {} different venue types and {} neighborhoods.'.format(
          Borough_name,
          len(Borough_neighborhoods['VenueCategory'].unique()),
          len(Borough_neighborhoods['Neighbourhood'].unique())))
    
    # create map of city using latitude and longitude values
    map_Borough = folium.Map(location=[Borough_latitude, Borough_longitude], zoom_start=10)

    # add markers to map
    for lat, lng, venue, category in zip(Borough_neighborhoods['VenueLatitude'], Borough_neighborhoods['VenueLongitude'], Borough_neighborhoods['Venue'], Borough_neighborhoods['VenueCategory']):
        label = '{}, {}'.format(category, venue)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=0.1,
            popup=label,
            color='red',
            fill=True,
            fill_color='#FF0000',
            fill_opacity=0.3).add_to(map_Borough)  

    return map_Borough

In [16]:
Venues_Map('Delhi, INDIA', D_venues)

The geographical coordinates of "Delhi, INDIA" are 28.6517178, 77.2219388.
The "Delhi, INDIA" dataframe has 226 different venue types and 172 neighborhoods.


In [17]:
D_venues.groupby('VenueCategory')['Venue'].count().sort_values(ascending=False)

VenueCategory
Indian Restaurant                  360
Hotel                              199
Café                               198
Coffee Shop                        147
Fast Food Restaurant               131
Pizza Place                        106
Chinese Restaurant                  96
Restaurant                          85
Bar                                 76
Market                              72
Light Rail Station                  67
Bakery                              59
Dessert Shop                        58
Asian Restaurant                    53
Italian Restaurant                  47
Clothing Store                      47
Snack Place                         46
Donut Shop                          45
Park                                42
Train Station                       41
Lounge                              39
Sandwich Place                      38
Metro Station                       35
Ice Cream Shop                      33
Shopping Mall                       33
Food Truck 

In [18]:
D_venues.groupby('Neighbourhood').count()

NeighbourhoodLatitude  NeighbourhoodLongitude  Venue  \
Neighbourhood                                                              
Adarsh Nagar                            8                       8      8   
Alaknanda                               8                       8      8   
Anand Vihar                             8                       8      8   
Ashok Nagar                            17                      17     17   
Ashok Vihar                            10                      10     10   
Azadpur                                 5                       5      5   
Babarpur                                8                       8      8   
Badarpur                                5                       5      5   
Bali Nagar                             25                      25     25   
Bara Hindu Rao                         24                      24     24   
Barakhamba Road                        90                      90     90   
Bawana                                  2                       2      2   
Begum Pur                              32                      32     32   
Brij Puri                               5                       5      5   
Chanakyapuri                           38                      38     38   
Chandni Chowk                          53                      53     53   
Chawri Bazaar                          21                      21     21   
Chhattarpur                             7                       7      7   
Chittaranjan Park                      55                      55     55   
Civil Lines                            11                      11     11   
Connaught Place                        79                      79     79   
Dabri, New Delhi                        5                       5      5   
Dariba Kalan                           28                      28     28   
Daryaganj                              16                      16     16   
Dayanand Colony                        55                      55     55   
Defence Colony                         38                      38     38   
Delhi Cantonment                        6                       6      6   
Dhaka                                   6                       6      6   
Dhaula Kuan                            66                      66     66   
Dilshad Garden                          6                       6      6   
Dwarka Sub City                         4                       4      4   
East Vinod Nagar                        5                       5      5   
East of Kailash                        43                      43     43   
Fateh Nagar                            14                      14     14   
Friends Colony                         11                      11     11   
Gandhi Nagar                            4                       4      4   
Gautampuri                              3                       3      3   
Geeta Colony                            5                       5      5   
Ghantewala                             12                      12     12   
Ghitorni                               12                      12     12   
Gole Market                            25                      25     25   
Golf Links                             62                      62     62   
Govindpuri                             10                      10     10   
Greater Kailash                        43                      43     43   
Green Park                             89                      89     89   
Gulabi Bagh                             4                       4      4   
Gulmohar Park                          40                      40     40   
Hauz Khas                              49                      49     49   
Hauz Khas Village                      80                      80     80   
INA Colony                             13                      13     13   
Inderpuri                               9                       9   

In [19]:
print('There are {} uniques categories.'.format(len(D_venues['VenueCategory'].unique())))

There are 226 uniques categories.


In [20]:
# one hot encoding
D_onehot = pd.get_dummies(D_venues[['VenueCategory']], prefix="", prefix_sep="")

#column lists before adding Neighbourhood
column_names = ['Neighbourhood'] + list(D_onehot.columns)

# add Neighbourhood column back to dataframe
D_onehot['Neighbourhood'] = D_venues['Neighbourhood'] 

# move Neighbourhood column to the first column
D_onehot = D_onehot[column_names]

D_onehot.head()

Neighbourhood  ATM  Accessories Store  Afghan Restaurant  \
0  Adarsh Nagar    0                  0                  0   
1  Adarsh Nagar    0                  0                  0   
2  Adarsh Nagar    0                  0                  0   
3  Adarsh Nagar    0                  0                  0   
4  Adarsh Nagar    0                  0                  0   

   African Restaurant  Airport  Airport Food Court  American Restaurant  \
0                   0        0                   0                    0   
1                   0        0                   0                    0   
2                   0        0                   0                    0   
3                   0        0                   0                    0   
4                   0        0                   0                    0   

   Antique Shop  Arcade  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0       0            0           0                    0   
1             0       0            0           0                    0   
2             0       0            0           0                    0   
3             0       0            0           0                    0   
4             0       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Australian Restaurant  BBQ Joint  \
0                 0                   0                      0          0   
1                 0                   0                      0          0   
2                 0                   0                      0          0   
3                 0                   0                      0          0   
4                 0                   0                      0          0   

   Bagel Shop  Bakery  Bank  Bar  Basketball Court  Bed & Breakfast  Beer Bar  \
0           0       0     0    0                 0                0         0   
1           0       1     0    0                 0                0         0   
2           0       0     0    0                 0                0         0   
3           0       0     0    0                 0                0         0   
4           0       0     0    0                 0                0         0   

   Beer Garden  Bengali Restaurant  Bistro  Boat or Ferry  Bookstore  \
0            0                   0       0              0          0   
1            0                   0       0              0          0   
2            0                   0       0              0          0   
3            0                   0       0              0          0   
4            0                   0       0              0          0   

   Botanical Garden  Boutique  Brazilian Restaurant  Breakfast Spot  Brewery  \
0                 0         0                     0               0        0   
1                 0         0                     0               0        0   
2                 0         0                     0               0        0   
3                 0         0                     0               0        0   
4                 0         0                     0               0        0   

   Bridal Shop  Buffet  Building  Burger Joint  Burmese Restaurant  \
0            0       0         0             0                   0   
1            0       0         0             0                   0   
2            0       0         0             0                   0   
3            0       0         0             0                   0   
4            0       0         0             0                   0   

   Burrito Place  Bus Station  Business Service  Cafeteria  Café  Campground  \
0              0            0                 0          0     0           0   
1              0            0                 0          0     0           0   
2              0            0                 0          0     0           0   
3              0            0                 0          0     0           0   
4              0            0                 0       

In [21]:
restaurant_List = []
search = 'Restaurant'
for i in D_onehot.columns :
    if search in i:
        restaurant_List.append(i)

In [22]:
restaurant_List

['Afghan Restaurant',
 'African Restaurant',
 'American Restaurant',
 'Asian Restaurant',
 'Australian Restaurant',
 'Bengali Restaurant',
 'Brazilian Restaurant',
 'Burmese Restaurant',
 'Chinese Restaurant',
 'Comfort Food Restaurant',
 'Dim Sum Restaurant',
 'Dumpling Restaurant',
 'Eastern European Restaurant',
 'English Restaurant',
 'Falafel Restaurant',
 'Fast Food Restaurant',
 'French Restaurant',
 'Halal Restaurant',
 'Indian Chinese Restaurant',
 'Indian Restaurant',
 'Italian Restaurant',
 'Japanese Restaurant',
 'Korean Restaurant',
 'Mediterranean Restaurant',
 'Mexican Restaurant',
 'Middle Eastern Restaurant',
 'Modern European Restaurant',
 'Molecular Gastronomy Restaurant',
 'Moroccan Restaurant',
 'Mughlai Restaurant',
 'Multicuisine Indian Restaurant',
 'North Indian Restaurant',
 'Northeast Indian Restaurant',
 'Portuguese Restaurant',
 'Punjabi Restaurant',
 'Restaurant',
 'Scandinavian Restaurant',
 'Seafood Restaurant',
 'South Indian Restaurant',
 'Spanish Rest

In [23]:
col_name = []
col_name = ['Neighbourhood'] + restaurant_List
D_restaurant = D_onehot[col_name]
D_restaurant = D_restaurant.iloc[:,::]

In [24]:
D_restaurant.head()

Neighbourhood  Afghan Restaurant  African Restaurant  American Restaurant  \
0  Adarsh Nagar                  0                   0                    0   
1  Adarsh Nagar                  0                   0                    0   
2  Adarsh Nagar                  0                   0                    0   
3  Adarsh Nagar                  0                   0                    0   
4  Adarsh Nagar                  0                   0                    0   

   Asian Restaurant  Australian Restaurant  Bengali Restaurant  \
0                 0                      0                   0   
1                 0                      0                   0   
2                 0                      0                   0   
3                 0                      0                   0   
4                 0                      0                   0   

   Brazilian Restaurant  Burmese Restaurant  Chinese Restaurant  \
0                     0                   0                   0   
1                     0                   0                   0   
2                     0                   0                   0   
3                     0                   0                   0   
4                     0                   0                   0   

   Comfort Food Restaurant  Dim Sum Restaurant  Dumpling Restaurant  \
0                        0                   0                    0   
1                        0                   0                    0   
2                        0                   0                    0   
3                        0                   0                    0   
4                        0                   0                    0   

   Eastern European Restaurant  English Restaurant  Falafel Restaurant  \
0                            0                   0                   0   
1                            0                   0                   0   
2                            0                   0                   0   
3                            0                   0                   0   
4                            0                   0                   0   

   Fast Food Restaurant  French Restaurant  Halal Restaurant  \
0                     0                  0                 0   
1                     0                  0                 0   
2                     0                  0                 0   
3                     0                  0                 0   
4                     0                  0                 0   

   Indian Chinese Restaurant  Indian Restaurant  Italian Restaurant  \
0                          0                  1                   0   
1                          0                  0                   0   
2                          0                  0                   0   
3                          0                  0                   0   
4                          0                  0                   0   

   Japanese Restaurant  Korean Restaurant  Mediterranean Restaurant  \
0                    0                  0                         0   
1                    0                  0                         0   
2                    0                  0                         0   
3                    0                  0                         0   
4                    0                  0                         0   

   Mexican Restaurant  Middle Eastern Restaurant  Modern European Restaurant  \
0                   0                          0                           0   
1                   0                          0                           0   
2                   0                          0                           0   
3                   0                          0                           0   
4                   0                          0                           0   

   Molecular Gastronomy Restaurant  Moroccan Restaurant  Mughlai Restaurant  \
0                                0                    0 

In [25]:
D_restaurant_grouped = D_restaurant.groupby('Neighbourhood').sum().reset_index()

In [26]:
D_restaurant_grouped.head(10)

Neighbourhood  Afghan Restaurant  African Restaurant  American Restaurant  \
0    Adarsh Nagar                  0                   0                    0   
1       Alaknanda                  0                   0                    0   
2     Anand Vihar                  0                   0                    0   
3     Ashok Nagar                  0                   0                    0   
4     Ashok Vihar                  0                   0                    0   
5         Azadpur                  0                   0                    0   
6        Babarpur                  0                   0                    0   
7        Badarpur                  0                   0                    0   
8      Bali Nagar                  0                   0                    1   
9  Bara Hindu Rao                  0                   0                    0   

   Asian Restaurant  Australian Restaurant  Bengali Restaurant  \
0                 0                      0                   0   
1                 0                      0                   0   
2                 0                      0                   0   
3                 0                      0                   0   
4                 1                      0                   0   
5                 0                      0                   0   
6                 0                      0                   0   
7                 0                      0                   0   
8                 0                      0                   0   
9                 2                      0                   0   

   Brazilian Restaurant  Burmese Restaurant  Chinese Restaurant  \
0                     0                   0                   0   
1                     0                   0                   0   
2                     0                   0                   0   
3                     0                   0                   1   
4                     0                   0                   0   
5                     0                   0                   0   
6                     0                   0                   0   
7                     0                   0                   0   
8                     0                   0                   2   
9                     0                   0                   0   

   Comfort Food Restaurant  Dim Sum Restaurant  Dumpling Restaurant  \
0                        0                   0                    0   
1                        0                   0                    0   
2                        0                   0                    0   
3                        0                   0                    0   
4                        0                   0                    0   
5                        0                   0                    0   
6                        0                   0                    0   
7                        0                   0                    0   
8                        0                   0                    0   
9                        0                   0                    0   

   Eastern European Restaurant  English Restaurant  Falafel Restaurant  \
0                            0                   0                   0   
1                            0                   0                   0   
2                            0                   0                   0   
3                            0                   0                   0   
4                            0                   0                   0   
5                            0                   0                   0   
6                            0                   0                   0   
7                            0                   0                   0   
8                            0                   0                   0   
9                            0                   0                   0   

   Fast Food Restaurant  French Restaurant  Halal 

In [27]:
D_restaurant_grouped['Total'] = D_restaurant_grouped .sum(axis=1)

In [28]:
D_restaurant_grouped.head(10)

Neighbourhood  Afghan Restaurant  African Restaurant  American Restaurant  \
0    Adarsh Nagar                  0                   0                    0   
1       Alaknanda                  0                   0                    0   
2     Anand Vihar                  0                   0                    0   
3     Ashok Nagar                  0                   0                    0   
4     Ashok Vihar                  0                   0                    0   
5         Azadpur                  0                   0                    0   
6        Babarpur                  0                   0                    0   
7        Badarpur                  0                   0                    0   
8      Bali Nagar                  0                   0                    1   
9  Bara Hindu Rao                  0                   0                    0   

   Asian Restaurant  Australian Restaurant  Bengali Restaurant  \
0                 0                      0                   0   
1                 0                      0                   0   
2                 0                      0                   0   
3                 0                      0                   0   
4                 1                      0                   0   
5                 0                      0                   0   
6                 0                      0                   0   
7                 0                      0                   0   
8                 0                      0                   0   
9                 2                      0                   0   

   Brazilian Restaurant  Burmese Restaurant  Chinese Restaurant  \
0                     0                   0                   0   
1                     0                   0                   0   
2                     0                   0                   0   
3                     0                   0                   1   
4                     0                   0                   0   
5                     0                   0                   0   
6                     0                   0                   0   
7                     0                   0                   0   
8                     0                   0                   2   
9                     0                   0                   0   

   Comfort Food Restaurant  Dim Sum Restaurant  Dumpling Restaurant  \
0                        0                   0                    0   
1                        0                   0                    0   
2                        0                   0                    0   
3                        0                   0                    0   
4                        0                   0                    0   
5                        0                   0                    0   
6                        0                   0                    0   
7                        0                   0                    0   
8                        0                   0                    0   
9                        0                   0                    0   

   Eastern European Restaurant  English Restaurant  Falafel Restaurant  \
0                            0                   0                   0   
1                            0                   0                   0   
2                            0                   0                   0   
3                            0                   0                   0   
4                            0                   0                   0   
5                            0                   0                   0   
6                            0                   0                   0   
7                            0                   0                   0   
8                            0                   0                   0   
9                            0                   0                   0   

   Fast Food Restaurant  French Restaurant  Halal 

In [29]:
D_grouped_clustering = D_restaurant_grouped.drop('Neighbourhood', 1)

for n_cluster in range(2, 10):
    kmeans = KMeans(n_clusters=n_cluster).fit(D_grouped_clustering)
    label = kmeans.labels_
    sil_coeff = silhouette_score(D_grouped_clustering, label, metric='euclidean')
    print("For n_clusters={}, The Silhouette Coefficient is {}".format(n_cluster, sil_coeff))

For n_clusters=2, The Silhouette Coefficient is 0.7254511601949276
For n_clusters=3, The Silhouette Coefficient is 0.6017717129448351
For n_clusters=4, The Silhouette Coefficient is 0.5344428917356605
For n_clusters=5, The Silhouette Coefficient is 0.4451882501292277
For n_clusters=6, The Silhouette Coefficient is 0.4279924791910529
For n_clusters=7, The Silhouette Coefficient is 0.34286898883230416
For n_clusters=8, The Silhouette Coefficient is 0.34780770267172834
For n_clusters=9, The Silhouette Coefficient is 0.4137319645835991


In [30]:
# set number of clusters
kclusters = 2

D_grouped_clustering = D_restaurant_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(D_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 0, 0, 1, 0, 1, 0,
       1, 0, 1, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0,
       1, 0, 0, 1, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0,
       1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [31]:
D_results = pd.DataFrame(kmeans.cluster_centers_)
D_results.columns = D_grouped_clustering.columns
D_results.index = ['cluster0','cluster1']
D_results['Total Sum'] = D_results.sum(axis = 1)
D_results

Afghan Restaurant  African Restaurant  American Restaurant  \
cluster0           0.006803        6.802721e-03             0.040816   
cluster1           0.040000        8.673617e-19             0.440000   

          Asian Restaurant  Australian Restaurant  Bengali Restaurant  \
cluster0           0.14966               0.027211            0.006803   
cluster1           1.24000               0.120000            0.080000   

          Brazilian Restaurant  Burmese Restaurant  Chinese Restaurant  \
cluster0         -7.806256e-18       -7.806256e-18            0.326531   
cluster1          4.000000e-02        4.000000e-02            1.920000   

          Comfort Food Restaurant  Dim Sum Restaurant  Dumpling Restaurant  \
cluster0            -7.806256e-18       -1.561251e-17             0.006803   
cluster1             4.000000e-02        8.000000e-02             0.040000   

          Eastern European Restaurant  English Restaurant  Falafel Restaurant  \
cluster0                -1.561251e-17       -7.806256e-18            0.006803   
cluster1                 8.000000e-02        4.000000e-02            0.040000   

          Fast Food Restaurant  French Restaurant  Halal Restaurant  \
cluster0              0.557823           0.020408      6.802721e-03   
cluster1              1.960000           0.440000      8.673617e-19   

          Indian Chinese Restaurant  Indian Restaurant  Italian Restaurant  \
cluster0              -1.561251e-17           1.081633            0.081633   
cluster1               8.000000e-02           8.040000            1.400000   

          Japanese Restaurant  Korean Restaurant  Mediterranean Restaurant  \
cluster0             0.040816           0.027211                  0.013605   
cluster1             0.520000           0.200000                  0.560000   

          Mexican Restaurant  Middle Eastern Restaurant  \
cluster0            0.006803               1.360544e-02   
cluster1            0.160000               1.734723e-18   

          Modern European Restaurant  Molecular Gastronomy Restaurant  \
cluster0                2.040816e-02                    -2.081668e-17   
cluster1                1.040834e-17                     1.200000e-01   

          Moroccan Restaurant  Mughlai Restaurant  \
cluster0         6.802721e-03        6.802721e-03   
cluster1         8.673617e-19        8.673617e-19   

          Multicuisine Indian Restaurant  North Indian Restaurant  \
cluster0                    6.802721e-03                 0.040816   
cluster1                    8.673617e-19                 0.120000   

          Northeast Indian Restaurant  Portuguese Restaurant  \
cluster0                     0.006803          -1.734723e-17   
cluster1                     0.040000           2.000000e-01   

          Punjabi Restaurant  Restaurant  Scandinavian Restaurant  \
cluster0        6.802721e-03    0.251701            -1.561251e-17   
cluster1        8.673617e-19    1.920000             8.000000e-02   

          Seafood Restaurant  South Indian Restaurant  Spanish Restaurant  \
cluster0            0.006803                 0.027211        6.802721e-03   
cluster1            0.120000                 0.400000        8.673617e-19   

          Tapas Restaurant  Tex-Mex Restaurant  Thai Restaurant  \
cluster0     -1.561251e-17       -1.561251e-17         0.047619   
cluster1      8.000000e-02        8.000000e-02         0.080000   

          Tibetan Restaurant  Turkish Restaurant  \
cluster0       -1.734723e-17       -1.561251e-17   
cluster1        2.000000e-01        8.000000e-02   

          Vegetarian / Vegan Restaurant  Vietnamese Restaurant      Total  \
cluster0                       0.020408          -2.081668e-17   2.884354   
cluster1                       0.120000           1.200000e-01  21.360000   

          Total Sum  
cluster0   5.768707  
cluster1  42.720000

In [32]:
D_results_merged = pd.DataFrame(D_restaurant_grouped['Neighbourhood'])

D_results_merged['Total'] = D_restaurant_grouped['Total']
D_results_merged = D_results_merged.assign(Cluster_Labels = kmeans.labels_)

In [33]:
print(D_results_merged.shape)
D_results_merged

(172, 3)


Neighbourhood  Total  Cluster_Labels
0          Adarsh Nagar      2               0
1             Alaknanda      3               0
2           Anand Vihar      1               0
3           Ashok Nagar      5               0
4           Ashok Vihar      3               0
5               Azadpur      1               0
6              Babarpur      0               0
7              Badarpur      2               0
8            Bali Nagar     10               0
9        Bara Hindu Rao      6               0
10      Barakhamba Road     31               1
11               Bawana      0               0
12            Begum Pur      9               0
13            Brij Puri      1               0
14         Chanakyapuri     15               1
15        Chandni Chowk     20               1
16        Chawri Bazaar      8               0
17          Chhattarpur      3               0
18    Chittaranjan Park     23               1
19          Civil Lines      4               0
20      Connaught Place     28               1
21     Dabri, New Delhi      2               0
22         Dariba Kalan     12               1
23            Daryaganj      5               0
24      Dayanand Colony     19               1
25       Defence Colony     16               1
26     Delhi Cantonment      1               0
27                Dhaka      1               0
28          Dhaula Kuan     26               1
29       Dilshad Garden      2               0
30      Dwarka Sub City      2               0
31     East Vinod Nagar      1               0
32      East of Kailash     14               1
33          Fateh Nagar      4               0
34       Friends Colony      1               0
35         Gandhi Nagar      1               0
36           Gautampuri      1               0
37         Geeta Colony      0               0
38           Ghantewala      3               0
39             Ghitorni      2               0
40          Gole Market      8               0
41           Golf Links     25               1
42           Govindpuri      4               0
43      Greater Kailash     11               0
44           Green Park     34               1
45          Gulabi Bagh      0               0
46        Gulmohar Park      9               0
47            Hauz Khas     14               1
48    Hauz Khas Village     29               1
49           INA Colony      5               0
50            Inderpuri      2               0
51         Jahangirpuri      0               0
52   Jamroodpur Village     16               1
53            Janakpuri      1               0
54             Jangpura      1               0
55               Jasola      3               0
56          Jhandewalan      6               0
57       Jhilmil Colony      2               0
58             Jor Bagh     10               0
59          Kabir Nagar      0               0
60       Kailash Colony     19               1
61              Kalkaji      5               0
62          Kamla Nagar      6               0
63           Karol Bagh      8               0
64        Kashmiri Gate      6               0
65         Keshav Puram      4               0
66          Khan Market     25               1
67              Khanpur      1               0
68       Khirki Village     27               1
69        Kingsway Camp      6               0
70          Kirby Place      0               0
71          Kirti Nagar      1               0
72   Kishangarh Village      1               0
73        Kohat Enclave      1               0
74     Kotla Mubarakpur     15               1
75              Kotwali      9               0
76        Krishna Nagar      0               0
77          Lahori Gate      2               0
78         Lajpat Nagar      7               0
79          Laxmi Nagar      2               0
80       Laxmibai Nagar      1               0
81          Lodi Colony      1               0
82        Maharani Bagh      1               0
83           Mahipalpur      5               0
84        Malvi

In [34]:
D_merged = DN_GEO

D_merged = D_merged.join(D_results_merged.set_index('Neighbourhood'), on='Neighbourhood')
D_merged.dropna(inplace=True)
print(D_merged.shape)
D_merged.head(10) # check the last columns!

(181, 6)


Districts  Neighbourhood   Latitude  Longitude  Total  \
0   North West Delhi   Adarsh Nagar  28.714200  77.166710    2.0   
1   North West Delhi    Ashok Vihar  28.692060  77.177550    3.0   
2   North West Delhi        Azadpur  28.705300  77.178300    1.0   
3   North West Delhi         Bawana  28.802210  77.040199    0.0   
4   North West Delhi      Begum Pur  28.536978  77.209941    9.0   
5   North West Delhi          Dhaka  28.708698  77.205749    1.0   
6   North West Delhi   Jahangirpuri  28.725987  77.162683    0.0   
8   North West Delhi   Keshav Puram  28.688914  77.161652    4.0   
9   North West Delhi  Kingsway Camp  28.698684  77.204675    6.0   
10  North West Delhi  Kohat Enclave  28.698014  77.140523    1.0   

    Cluster_Labels  
0              0.0  
1              0.0  
2              0.0  
3              0.0  
4              0.0  
5              0.0  
6              0.0  
8              0.0  
9              0.0  
10             0.0

In [35]:
#D_merged.drop([7,54,107], axis=0,inplace=True)

In [36]:
#D_merged.reset_index(drop=True,inplace=True)

In [37]:
#D_merged.drop([53], axis=0,inplace=True)

In [38]:
D_merged[['Total','Cluster_Labels']] =D_merged[['Total','Cluster_Labels']].astype(int)

In [39]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(D_merged['Latitude'], D_merged['Longitude'], D_merged['Neighbourhood'], D_merged['Cluster_Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [40]:
D_merged[D_merged['Cluster_Labels'] == 1].reset_index(drop=True)

Districts       Neighbourhood   Latitude  Longitude  Total  \
0        North Delhi       Chandni Chowk  28.659731  77.234459     20   
1        North Delhi        Dariba Kalan  28.654602  77.233379     12   
2        North Delhi           Paharganj  28.641499  77.214061     31   
3   North East Delhi        Shastri Park  28.632730  77.220020     28   
4      Central Delhi       Chandni Chowk  28.656076  77.230740     20   
5      Central Delhi           Paharganj  28.642261  77.215522     31   
6      Central Delhi      Rajender Nagar  28.641949  77.185690     13   
7          New Delhi     Barakhamba Road  28.629517  77.225470     31   
8          New Delhi        Chanakyapuri  28.591530  77.171890     15   
9          New Delhi     Connaught Place  28.632800  77.219800     28   
10         New Delhi          Golf Links  28.598900  77.231700     25   
11         New Delhi         Khan Market  28.600342  77.226920     25   
12       South Delhi   Chittaranjan Park  28.540200  77.248100     23   
13       South Delhi     Dayanand Colony  28.468071  77.065240     19   
14       South Delhi      Defence Colony  28.573400  77.230700     16   
15       South Delhi     East of Kailash  28.557080  77.244521     14   
16       South Delhi          Green Park  28.556775  77.203736     34   
17       South Delhi           Hauz Khas  28.550475  77.207776     14   
18       South Delhi   Hauz Khas Village  28.554310  77.195140     29   
19       South Delhi  Jamroodpur Village  28.557100  77.236900     16   
20       South Delhi      Kailash Colony  28.553800  77.242000     19   
21       South Delhi      Khirki Village  28.531065  77.218549     27   
22       South Delhi    Kotla Mubarakpur  28.574311  77.224925     15   
23       South Delhi       Malviya Nagar  28.535300  77.210900     14   
24       South Delhi        Netaji Nagar  28.576188  77.186575     14   
25       South Delhi      Sarojini Nagar  28.579500  77.197100     26   
26  South West Delhi         Dhaula Kuan  28.597010  77.164612     26   
27  South West Delhi      Sarojini Nagar  28.579500  77.197100     26   
28        West Delhi         Dhaula Kuan  28.597010  77.164612     26   

    Cluster_Labels  
0                1  
1                1  
2                1  
3                1  
4                1  
5                1  
6                1  
7                1  
8                1  
9                1  
10               1  
11               1  
12               1  
13               1  
14               1  
15               1  
16               1  
17               1  
18               1  
19               1  
20               1  
21               1  
22               1  
23               1  
24               1  
25               1  
26               1  
27               1  
28               1

In [41]:
D_merged[D_merged['Total'] == 0].reset_index(drop=True)

Districts       Neighbourhood   Latitude  Longitude  Total  \
0   North West Delhi              Bawana  28.802210  77.040199      0   
1   North West Delhi        Jahangirpuri  28.725987  77.162683      0   
2   North West Delhi     Rohini Sub City  28.737320  77.090980      0   
3        North Delhi        Shakti Nagar  28.678699  77.195168      0   
4        North Delhi         Gulabi Bagh  28.675172  77.189837      0   
5        North Delhi         Pul Bangash  28.666376  77.207421      0   
6        North Delhi      Roshanara Bagh  28.673718  77.199320      0   
7        North Delhi        Sangam Vihar  28.497702  77.239174      0   
8        North Delhi     Sarai Kale Khan  28.586626  77.256228      0   
9        North Delhi       Sarai Rohilla  28.667873  77.190267      0   
10       North Delhi        Shakti Nagar  28.678699  77.195168      0   
11  North East Delhi            Babarpur  28.687542  77.280539      0   
12  North East Delhi         Kabir Nagar  28.686327  77.187898      0   
13  North East Delhi             Mandoli  28.705566  77.316689      0   
14  North East Delhi             Maujpur  28.689589  77.274074      0   
15  North East Delhi        New Usmanpur  28.680458  77.259323      0   
16  North East Delhi            Sadatpur  28.721623  77.262839      0   
17  North East Delhi        Yamuna Vihar  28.699609  77.274474      0   
18        East Delhi        Geeta Colony  28.652029  77.270884      0   
19        East Delhi       Krishna Nagar  28.659750  77.282550      0   
20        East Delhi  Vasundhara Enclave  28.600600  77.319100      0   
21       South Delhi       Pulpehaladpur  28.499400  77.291800      0   
22       South Delhi         Tughlaqabad  28.514900  77.268800      0   
23  South West Delhi         Kirby Place  28.607323  77.125631      0   
24  South West Delhi           Najafgarh  28.612500  76.984720      0   
25  South West Delhi             Rajokri  28.503100  77.111060      0   
26  South West Delhi            Rangpuri  28.533942  77.114579      0   
27        West Delhi        Partap Nagar  28.670106  77.195115      0   

    Cluster_Labels  
0                0  
1                0  
2                0  
3                0  
4                0  
5                0  
6                0  
7                0  
8                0  
9                0  
10               0  
11               0  
12               0  
13               0  
14               0  
15               0  
16               0  
17               0  
18               0  
19               0  
20               0  
21               0  
22               0  
23               0  
24               0  
25               0  
26               0  
27               0